In [ ]:
# 安装 torch torchaudio torchvision
!pip install torch==2.0.0+cu118 torchaudio==2.0.1+cu118 torchvision==0.15.1+cu118 --index-url https://download.pytorch.org/whl/cu118

development

In [24]:
import torch
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:  
 print('Not connected to a GPU')
else:  
 print(gpu_info)
use_cuda = torch.cuda.is_available()

Sat Jan 31 18:31:38 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 576.40                 Driver Version: 576.40         CUDA Version: 12.9     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3090      WDDM  |   00000000:01:00.0  On |                  N/A |
|  0%   50C    P8             29W /  390W |   21253MiB /  24576MiB |     14%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [25]:
SEED = 42
WEIGHTED = True

In [26]:
from datasets import *
import pandas as pd
import numpy as np
train = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/spa", split="train"))
val = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/spa", split="train"))
test = pd.DataFrame(load_dataset("dev_phase2/subtask3/dev/spa", split="train"))
test_final = pd.DataFrame(load_dataset("test_phase/subtask3/test/spa", split="train"))
train.head()

id  \
0  spa_bc7bf0a1b710cd724cf96b5eeb020bff   
1  spa_688aec0f6abf4e0be44ecbfa886251cc   
2  spa_47019efabe7295c630bcc04bd0429230   
3  spa_8b4b244dbb90e0a813661ed12a1af5af   
4  spa_e2f37881da08b8d7b6eb07bc37356746   

                                                text  stereotype  \
0  "bueno, tirando"\ny si hay repregunta, entonce...           0   
1                "caimos en su retorica de indigena"           0   
2   "cara de indigena sudaca", porque pio asi luego?           0   
3  "violar a una nina es menos grave que un abort...           0   
4              "yo decido quien es judio y quien no"           1   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             1               0                 1                0   
4             0               1                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0

In [27]:
labels = ["stereotype", "vilification", "dehumanization", "extreme_language", "lack_of_empathy", "invalidation"]
def get_text_and_label(df):  
  return df.rename(columns={"text": "text"})[["text"] + labels]
train = get_text_and_label(train)
print(f"Dataset size: <{len(train.index)}:{len(val.index)}:{len(test.index)}:{len(test_final.index)}>")
train.head(10)

Dataset size: <3305:3305:165:1488>


text  stereotype  \
0  "bueno, tirando"\ny si hay repregunta, entonce...           0   
1                "caimos en su retorica de indigena"           0   
2   "cara de indigena sudaca", porque pio asi luego?           0   
3  "violar a una nina es menos grave que un abort...           0   
4              "yo decido quien es judio y quien no"           1   
5  #8m e cada dia en defensa dun xornalismo femin...           0   
6  #chvnoticias la muerte de ninos no se transa p...           0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...           1   
8  #ecuador | la cancilleria implementa plan de a...           0   
9  #importante | te decimos la ubicacion de los 1...           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             1               0                 1                0   
4             0               1                 0                0   
5             0               0                 0                0   
6             0               1                 0                1   
7             1               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             1  
8             0  
9             0

In [28]:
val = get_text_and_label(val)
val.head(10)

text  stereotype  \
0  "bueno, tirando"\ny si hay repregunta, entonce...           0   
1                "caimos en su retorica de indigena"           0   
2   "cara de indigena sudaca", porque pio asi luego?           0   
3  "violar a una nina es menos grave que un abort...           0   
4              "yo decido quien es judio y quien no"           1   
5  #8m e cada dia en defensa dun xornalismo femin...           0   
6  #chvnoticias la muerte de ninos no se transa p...           0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...           1   
8  #ecuador | la cancilleria implementa plan de a...           0   
9  #importante | te decimos la ubicacion de los 1...           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             1               0                 1                0   
4             0               1                 0                0   
5             0               0                 0                0   
6             0               1                 0                1   
7             1               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             1  
8             0  
9             0

In [29]:
test = get_text_and_label(test)
test.head(10)

text stereotype vilification  \
0  "puta weon, los progres arruinaron el indio pi...       None         None   
1  #mexico | el gobierno informo que esta dialoga...       None         None   
2               a abortar el mojon que traen atorado       None         None   
3             a comerrrrr\n(la salsa es curry indio)       None         None   
4                         aborto libre y retroactivo       None         None   
5  ah, veo que te has saltado las secuelas y el r...       None         None   
6            ase sina y corrupta , ella y su sequito       None         None   
7                           chak de india\n#indvseng       None         None   
8          coincred, a digital india.\n#coincredweb3       None         None   
9  corrupcion, corrupcion corrutos corrutos corru...       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [30]:
test_final = get_text_and_label(test_final)
test_final.head(10)

text stereotype vilification  \
0  "penas severas para el aborto porque yo estuve...       None         None   
1              "si eres pobre debes abortar" eso lei       None         None   
2  #brasil exige a #eeuu "respeto" para repatriad...       None         None   
3  #honduras | el canciller anuncio la llegada de...       None         None   
4  #internacionales | el presidente de colombia, ...       None         None   
5            #karolsevilla #laliarg #kcamexico indio       None         None   
6  #mafiachotana #organizacioncriminal #corrupcio...       None         None   
7        , si tu no quieres, no tiene porque abortar       None         None   
8  -queee? pero si elon musk es judio.\n_y que ac...       None         None   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [31]:
def generate_multilabel_df(df):
  df["labels"] = np.empty((len(df), len(labels))).tolist()
  for index, row in df.iterrows():
    row_labels = [row[label] for label in labels]
    for i in range(len(labels)):
      df.loc[index, "labels"][i] = row_labels[i]
  return df[["text", "labels"]]
train = generate_multilabel_df(train)
val = generate_multilabel_df(val)
test = generate_multilabel_df(test)
test_final = generate_multilabel_df(test_final)
train.head(10)

text              labels
0  "bueno, tirando"\ny si hay repregunta, entonce...  [0, 0, 0, 0, 0, 0]
1                "caimos en su retorica de indigena"  [0, 0, 0, 0, 0, 0]
2   "cara de indigena sudaca", porque pio asi luego?  [0, 0, 0, 0, 0, 0]
3  "violar a una nina es menos grave que un abort...  [0, 1, 0, 1, 0, 0]
4              "yo decido quien es judio y quien no"  [1, 0, 1, 0, 0, 0]
5  #8m e cada dia en defensa dun xornalismo femin...  [0, 0, 0, 0, 0, 0]
6  #chvnoticias la muerte de ninos no se transa p...  [0, 0, 1, 0, 1, 0]
7  #corrupcion#prensa#desestabilizadora#nido#rata...  [1, 1, 0, 0, 0, 1]
8  #ecuador | la cancilleria implementa plan de a...  [0, 0, 0, 0, 0, 0]
9  #importante | te decimos la ubicacion de los 1...  [0, 0, 0, 0, 0, 0]

In [32]:
test.head(10)

text  \
0  "puta weon, los progres arruinaron el indio pi...   
1  #mexico | el gobierno informo que esta dialoga...   
2               a abortar el mojon que traen atorado   
3             a comerrrrr\n(la salsa es curry indio)   
4                         aborto libre y retroactivo   
5  ah, veo que te has saltado las secuelas y el r...   
6            ase sina y corrupta , ella y su sequito   
7                           chak de india\n#indvseng   
8          coincred, a digital india.\n#coincredweb3   
9  corrupcion, corrupcion corrutos corrutos corru...   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [33]:
test_final.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [34]:
from datetime import datetime, timedelta
import os
PATH = "./outputs/{}/".format((datetime.now() + timedelta(hours=2)).strftime("%d-%m-%Y-%H-%M"))
print("Current working dir:", PATH)
os.mkdir(PATH)

Current working dir: ./outputs/31-01-2026-20-32/


In [35]:
models = {
    "mbert-cased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-cased"
    },
    "mbert-uncased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-uncased"
    },
    "roberta": {
        "model_type": "roberta",
        "model_name": "models--FacebookAI--roberta-base"
    },
    "beto-cased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-cased"
    },
    "beto-uncased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-uncased"
    },
    "distilbert-multi": {
        "model_type": "distilbert",
        "model_name": "models--distilbert--distilbert-base-multilingual-cased"
    }
}

In [36]:
from simpletransformers.classification import MultiLabelClassificationModel, MultiLabelClassificationArgs
for model, fields in models.items():
  model_args = MultiLabelClassificationArgs(
      overwrite_output_dir= True,
      eval_batch_size=8,
      num_train_epochs=5,
      learning_rate = 4e-05,
      optimizer="AdamW",
      manual_seed=SEED,
      use_early_stopping=True,
      save_model_every_epoch=False
  )
  model_args.output_dir = os.path.join(PATH, model)
  models[model] = MultiLabelClassificationModel(fields["model_type"], fields["model_name"],
                                      args=model_args, num_labels=len(labels), use_cuda=use_cuda)

Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--FacebookAI--roberta-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.dense.bias', 'roberta.pooler.dense.weight', 'classifier.dense.weight', 'roberta.pooler.dense.bias', 'classifier.out_

In [37]:
from sklearn.metrics import mean_squared_error
from math import sqrt
def root_mean_squared_error(y_true, y_pred):    
  return sqrt(mean_squared_error(y_true, y_pred))

In [ ]:
for model_name, model in models.items():
  model.train_model(train, loss_fct=root_mean_squared_error)

7it [00:04,  1.55it/s]                                                                                                                                                                                                                  
Epoch 5 of 5: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [02:57<00:00, 35.51s/it]
7it [00:05,  1.25it/s]                                                                                                                                                                                                                  
Epochs 2/5. Running Loss:    0.2545:  48%|███████████████████████████████████████████████████████████████████████████▎                                                                                | 200/414 [00:13<00:13, 16.12it/s]

Epochs 5/5. Running Loss:    0.3860:  93%|█████████████████████████

In [49]:
import collections
from itertools import combinations
models_names = list(models.keys())
ensembles_list = list()
for i in range(1, len(models_names) + 1):
    ensembles_list += list(combinations(models_names, i))
ensembles_list = [list(ensemble) for ensemble in ensembles_list]
ensembles = {}
for i in range(len(ensembles_list)):
  ensembles["ensemble{:02d}".format(i)] = {}
  ensembles["ensemble{:02d}".format(i)]["models"] = ensembles_list[i]
  ensembles["ensemble{:02d}".format(i)]["metrics"] = {}
ensembles

{'ensemble00': {'models': ['mbert-cased'], 'metrics': {}},
 'ensemble01': {'models': ['mbert-uncased'], 'metrics': {}},
 'ensemble02': {'models': ['roberta'], 'metrics': {}},
 'ensemble03': {'models': ['beto-cased'], 'metrics': {}},
 'ensemble04': {'models': ['beto-uncased'], 'metrics': {}},
 'ensemble05': {'models': ['distilbert-multi'], 'metrics': {}},
 'ensemble06': {'models': ['mbert-cased', 'mbert-uncased'], 'metrics': {}},
 'ensemble07': {'models': ['mbert-cased', 'roberta'], 'metrics': {}},
 'ensemble08': {'models': ['mbert-cased', 'beto-cased'], 'metrics': {}},
 'ensemble09': {'models': ['mbert-cased', 'beto-uncased'], 'metrics': {}},
 'ensemble10': {'models': ['mbert-cased', 'distilbert-multi'], 'metrics': {}},
 'ensemble11': {'models': ['mbert-uncased', 'roberta'], 'metrics': {}},
 'ensemble12': {'models': ['mbert-uncased', 'beto-cased'], 'metrics': {}},
 'ensemble13': {'models': ['mbert-uncased', 'beto-uncased'], 'metrics': {}},
 'ensemble14': {'models': ['mbert-uncased', 'd

In [50]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, f1_score
def compute_metrics(y_true, y_pred):
  macro_precision, macro_recall, macro_f1, _ = precision_recall_fscore_support(y_true, y_pred, average='macro')
  acc = accuracy_score(y_true, y_pred)
  weighted_f1 = f1_score(y_true, y_pred, average='weighted')
  return {
      'accuracy': round(acc, 5),
      'macro_f1': round(macro_f1, 5),
      'macro_precision': round(macro_precision, 5),
      'macro_recall': round(macro_recall, 5),
      'weighted_f1': round(weighted_f1, 5)
  }
model_evaluation = {}
for model_name in models:
  model_evaluation[model_name] = {}
  result, model_outputs, wrong_predictions = models[model_name].eval_model(val, metric=root_mean_squared_error)
  model_evaluation[model_name]["result"] = result                                                                   
  model_evaluation[model_name]["val_model_outputs"] = model_outputs                                                 
  model_evaluation[model_name]["val_predictions"] = list ()
  for output in model_outputs:
    model_evaluation[model_name]["val_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output]) 
  model_evaluation[model_name]["val_wrong_predictions"] = wrong_predictions                                         
  model_evaluation[model_name]["metrics"] = compute_metrics(val.get("labels").tolist(), model_evaluation[model_name].get("val_predictions"))
  print(f"{model_name}\t", model_evaluation[model_name].get("metrics"))

7it [00:05,  1.37it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 74.70it/s]
C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


mbert-cased	 {'accuracy': 0.48593, 'macro_f1': 0.09524, 'macro_precision': 0.21917, 'macro_recall': 0.06901, 'weighted_f1': 0.13432}


7it [00:04,  1.47it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 82.14it/s]


mbert-uncased	 {'accuracy': 0.68502, 'macro_f1': 0.78183, 'macro_precision': 0.80908, 'macro_recall': 0.76351, 'weighted_f1': 0.80199}


7it [00:04,  1.50it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 80.09it/s]
C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


...

beto-cased	 {'accuracy': 0.83419, 'macro_f1': 0.90314, 'macro_precision': 0.92223, 'macro_recall': 0.8869, 'weighted_f1': 0.91059}


7it [00:04,  1.62it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:04<00:00, 82.95it/s]


beto-uncased	 {'accuracy': 0.89652, 'macro_f1': 0.94597, 'macro_precision': 0.95126, 'macro_recall': 0.94179, 'weighted_f1': 0.94973}


7it [00:04,  1.56it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:02<00:00, 140.96it/s]


distilbert-multi	 {'accuracy': 0.66717, 'macro_f1': 0.7647, 'macro_precision': 0.80855, 'macro_recall': 0.7337, 'weighted_f1': 0.78447}


In [51]:
from sklearn.preprocessing import normalize
def vote(predictions, weighted=False, weights=None):
  votes = list()  
  for i in range(len(labels)):    
    curr_label_preds = [preds[i] for preds in predictions]    
    voting = sum(curr_label_preds * weights) if weighted else sum(curr_label_preds)/len(curr_label_preds)
    votes.append(0 if voting < 0.5 else 1)  
  return votes
ensemble_evaluation = {}
def predict_ensemble(ensemble_name, dataset_name, dataset, weighted=False):
  ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"] = list()  
  for i in range(len(dataset.index)):
    predictions = list()
    ensemble_models = ensembles[ensemble_name].get("models")      
    for model_name in ensemble_models:
      curr_model_outputs = model_evaluation[model_name].get(f"{dataset_name}_model_outputs")
      predictions.append(curr_model_outputs[i])
    weights = list()    
    if weighted:      
      f1_scores_list = [model_evaluation[model_name]["metrics"].get("weighted_f1")                        
                        for model_name in ensembles[ensemble_name].get("models")]
      weights = normalize([f1_scores_list], norm="l1")[0]
    ensemble_pred = vote(predictions, weighted, weights)
    ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"].append(ensemble_pred)
for ensemble_name in ensembles:
  ensemble_evaluation[ensemble_name] = {}
  ensemble_evaluation[ensemble_name]["val_predictions"] = list()
  predict_ensemble(ensemble_name, "val", val, weighted=WEIGHTED)
  ensembles[ensemble_name]["metrics"] = compute_metrics(val.get("labels").tolist(), ensemble_evaluation[ensemble_name].get("val_predictions"))  
  print(f"{ensemble_name}\t", ensembles[ensemble_name].get("metrics"))

C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


ensemble00	 {'accuracy': 0.48593, 'macro_f1': 0.09524, 'macro_precision': 0.21917, 'macro_recall': 0.06901, 'weighted_f1': 0.13432}
ensemble01	 {'accuracy': 0.68502, 'macro_f1': 0.78183, 'macro_precision': 0.80908, 'macro_recall': 0.76351, 'weighted_f1': 0.80199}


C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


ensemble02	 {'accuracy': 0.49773, 'macro_f1': 0.0, 'macro_precision': 0.0, 'macro_recall': 0.0, 'weighted_f1': 0.0}
ensemble03	 {'accuracy': 0.83419, 'macro_f1': 0.90314, 'macro_precision': 0.92223, 'macro_recall': 0.8869, 'weighted_f1': 0.91059}
ensemble04	 {'accuracy': 0.89652, 'macro_f1': 0.94597, 'macro_precision': 0.95126, 'macro_recall': 0.94179, 'weighted_f1': 0.94973}
ensemble05	 {'accuracy': 0.66717, 'macro_f1': 0.7647, 'macro_precision': 0.80855, 'macro_recall': 0.7337, 'weighted_f1': 0.78447}
ensemble06	 {'accuracy': 0.67776, 'macro_f1': 0.76978, 'macro_precision': 0.82968, 'macro_recall': 0.72927, 'weighted_f1': 0.79385}


C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


ensemble07	 {'accuracy': 0.48593, 'macro_f1': 0.09524, 'macro_precision': 0.21917, 'macro_recall': 0.06901, 'weighted_f1': 0.13432}
ensemble08	 {'accuracy': 0.82844, 'macro_f1': 0.89611, 'macro_precision': 0.93396, 'macro_recall': 0.86554, 'weighted_f1': 0.90592}
ensemble09	 {'accuracy': 0.89319, 'macro_f1': 0.94165, 'macro_precision': 0.95632, 'macro_recall': 0.92938, 'weighted_f1': 0.94699}
ensemble10	 {'accuracy': 0.65749, 'macro_f1': 0.74022, 'macro_precision': 0.83343, 'macro_recall': 0.68437, 'weighted_f1': 0.7679}
ensemble11	 {'accuracy': 0.68502, 'macro_f1': 0.78183, 'macro_precision': 0.80908, 'macro_recall': 0.76351, 'weighted_f1': 0.80199}
ensemble12	 {'accuracy': 0.80454, 'macro_f1': 0.88343, 'macro_precision': 0.9154, 'macro_recall': 0.85823, 'weighted_f1': 0.89358}
ensemble13	 {'accuracy': 0.8711, 'macro_f1': 0.92657, 'macro_precision': 0.94034, 'macro_recall': 0.91535, 'weighted_f1': 0.93448}
ensemble14	 {'accuracy': 0.69803, 'macro_f1': 0.79327, 'macro_precision': 0.841

In [52]:
import json
with open(os.path.join(PATH, 'ensembles.json'), 'w', encoding='utf-8') as f:
    json.dump(ensembles, f, ensure_ascii=False, indent=4)

In [53]:
f1_scores = {ensemble_name: ensembles[ensemble_name]["metrics"].get("weighted_f1") for ensemble_name in ensemble_evaluation}
best_ensemble_name = max(f1_scores, key=f1_scores.get)
best_ensemble = {"name": best_ensemble_name,                 
                "models": ensembles[best_ensemble_name].get("models"),                 
                "metrics": ensembles[best_ensemble_name].get("metrics")                 
                }
best_ensemble

{'name': 'ensemble18',
 'models': ['beto-cased', 'beto-uncased'],
 'metrics': {'accuracy': 0.90469,
  'macro_f1': 0.9484,
  'macro_precision': 0.95785,
  'macro_recall': 0.94031,
  'weighted_f1': 0.95304}}

In [54]:
for model_name in models:
  model_predictions, model_raw_outputs = models.get(model_name).predict(test["text"].tolist())
  model_evaluation[model_name]["test_model_outputs"] = model_raw_outputs
  model_evaluation[model_name]["test_predictions"] = list ()  
  for output in model_raw_outputs:
    model_evaluation[model_name]["test_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output])
predict_ensemble(best_ensemble.get("name"), "test", test, weighted=WEIGHTED)

1it [00:03,  3.26s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [00:00<00:00, 47.64it/s]
1it [00:03,  3.29s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [00:00<00:00, 44.79it/s]
1it [00:03,  3.47s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [00:00<00:00, 44.46it/s]
1it [00:03,  3.24s/it]
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 21/21 [

In [55]:
for model_name, evaluation in model_evaluation.items():
  curr_model = model_evaluation.get(model_name)
  curr_model["val_model_outputs"] = [list(output) for output in curr_model.get("val_model_outputs")]
  curr_model["test_model_outputs"] = [list(output) for output in curr_model.get("test_model_outputs")]
  curr_model["val_predictions"] = list(curr_model.get("val_predictions"))
  curr_model["test_predictions"] = list(curr_model.get("test_predictions"))
  if curr_model.get("val_wrong_predictions"):
    curr_model["val_wrong_predictions_list"] = curr_model.get("val_wrong_predictions")
    curr_model["val_wrong_predictions"] = {}
    for pred in curr_model.get("val_wrong_predictions_list"):
      curr_model["val_wrong_predictions"][pred.guid] = {
          "text_a": pred.text_a,
          "text_b": pred.text_b,
          "label": pred.label
      }
    del curr_model["val_wrong_predictions_list"]

  with open(os.path.join(PATH, f'{model_name}/model-evaluation.json'), 'w', encoding='utf-8') as f:
    json.dump(curr_model, f, ensure_ascii=False, indent=4)

In [56]:
best_ensemble["val_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("val_predictions")
best_ensemble["test_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
with open(os.path.join(PATH, 'best-ensemble.json'), 'w', encoding='utf-8') as f:
    json.dump(best_ensemble, f, ensure_ascii=False, indent=4)

In [57]:
test["predicted_labels"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
test.head(10)

text  \
0  "puta weon, los progres arruinaron el indio pi...   
1  #mexico | el gobierno informo que esta dialoga...   
2               a abortar el mojon que traen atorado   
3             a comerrrrr\n(la salsa es curry indio)   
4                         aborto libre y retroactivo   
5  ah, veo que te has saltado las secuelas y el r...   
6            ase sina y corrupta , ella y su sequito   
7                           chak de india\n#indvseng   
8          coincred, a digital india.\n#coincredweb3   
9  corrupcion, corrupcion corrutos corrutos corru...   

                                 labels    predicted_labels  
0  [None, None, None, None, None, None]  [0, 1, 0, 1, 0, 0]  
1  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
2  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
3  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
4  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
5  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
6  [None, None, None, None, None, None]  [0, 1, 0, 0, 0, 1]  
7  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
8  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
9  [None, None, None, None, None, None]  [1, 1, 0, 0, 1, 1]

In [58]:
test.to_csv(os.path.join(PATH, "test-predictions.csv"), index=False)  

test

In [59]:
import torch
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:  
 print('Not connected to a GPU')
else:  
 print(gpu_info)
use_cuda = torch.cuda.is_available()

Sat Jan 31 20:51:34 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 576.40                 Driver Version: 576.40         CUDA Version: 12.9     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                  Driver-Model | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA GeForce RTX 3090      WDDM  |   00000000:01:00.0  On |                  N/A |
|  0%   42C    P8             27W /  390W |   23755MiB /  24576MiB |      8%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [60]:
SEED = 42
WEIGHTED = True

In [61]:
from datasets import *
import pandas as pd
import numpy as np
train = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/spa", split="train"))
val = pd.DataFrame(load_dataset("dev_phase2/subtask3/train/spa", split="train"))
test = pd.DataFrame(load_dataset("dev_phase2/subtask3/dev/spa", split="train"))
test_final = pd.DataFrame(load_dataset("test_phase/subtask3/test/spa", split="train"))
train.head()

id  \
0  spa_bc7bf0a1b710cd724cf96b5eeb020bff   
1  spa_688aec0f6abf4e0be44ecbfa886251cc   
2  spa_47019efabe7295c630bcc04bd0429230   
3  spa_8b4b244dbb90e0a813661ed12a1af5af   
4  spa_e2f37881da08b8d7b6eb07bc37356746   

                                                text  stereotype  \
0  "bueno, tirando"\ny si hay repregunta, entonce...           0   
1                "caimos en su retorica de indigena"           0   
2   "cara de indigena sudaca", porque pio asi luego?           0   
3  "violar a una nina es menos grave que un abort...           0   
4              "yo decido quien es judio y quien no"           1   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             1               0                 1                0   
4             0               1                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0

In [62]:
labels = ["stereotype", "vilification", "dehumanization", "extreme_language", "lack_of_empathy", "invalidation"]
def get_text_and_label(df):  
  return df.rename(columns={"text": "text"})[["text"] + labels]
train = get_text_and_label(train)
print(f"Dataset size: <{len(train.index)}:{len(val.index)}:{len(test.index)}:{len(test_final.index)}>")
train.head(10)

Dataset size: <3305:3305:165:1488>


text  stereotype  \
0  "bueno, tirando"\ny si hay repregunta, entonce...           0   
1                "caimos en su retorica de indigena"           0   
2   "cara de indigena sudaca", porque pio asi luego?           0   
3  "violar a una nina es menos grave que un abort...           0   
4              "yo decido quien es judio y quien no"           1   
5  #8m e cada dia en defensa dun xornalismo femin...           0   
6  #chvnoticias la muerte de ninos no se transa p...           0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...           1   
8  #ecuador | la cancilleria implementa plan de a...           0   
9  #importante | te decimos la ubicacion de los 1...           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             1               0                 1                0   
4             0               1                 0                0   
5             0               0                 0                0   
6             0               1                 0                1   
7             1               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             1  
8             0  
9             0

In [63]:
val = get_text_and_label(val)
val.head(10)

text  stereotype  \
0  "bueno, tirando"\ny si hay repregunta, entonce...           0   
1                "caimos en su retorica de indigena"           0   
2   "cara de indigena sudaca", porque pio asi luego?           0   
3  "violar a una nina es menos grave que un abort...           0   
4              "yo decido quien es judio y quien no"           1   
5  #8m e cada dia en defensa dun xornalismo femin...           0   
6  #chvnoticias la muerte de ninos no se transa p...           0   
7  #corrupcion#prensa#desestabilizadora#nido#rata...           1   
8  #ecuador | la cancilleria implementa plan de a...           0   
9  #importante | te decimos la ubicacion de los 1...           0   

   vilification  dehumanization  extreme_language  lack_of_empathy  \
0             0               0                 0                0   
1             0               0                 0                0   
2             0               0                 0                0   
3             1               0                 1                0   
4             0               1                 0                0   
5             0               0                 0                0   
6             0               1                 0                1   
7             1               0                 0                0   
8             0               0                 0                0   
9             0               0                 0                0   

   invalidation  
0             0  
1             0  
2             0  
3             0  
4             0  
5             0  
6             0  
7             1  
8             0  
9             0

In [64]:
test = get_text_and_label(test)
test.head(10)

text stereotype vilification  \
0  "puta weon, los progres arruinaron el indio pi...       None         None   
1  #mexico | el gobierno informo que esta dialoga...       None         None   
2               a abortar el mojon que traen atorado       None         None   
3             a comerrrrr\n(la salsa es curry indio)       None         None   
4                         aborto libre y retroactivo       None         None   
5  ah, veo que te has saltado las secuelas y el r...       None         None   
6            ase sina y corrupta , ella y su sequito       None         None   
7                           chak de india\n#indvseng       None         None   
8          coincred, a digital india.\n#coincredweb3       None         None   
9  corrupcion, corrupcion corrutos corrutos corru...       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [65]:
test_final = get_text_and_label(test_final)
test_final.head(10)

text stereotype vilification  \
0  "penas severas para el aborto porque yo estuve...       None         None   
1              "si eres pobre debes abortar" eso lei       None         None   
2  #brasil exige a #eeuu "respeto" para repatriad...       None         None   
3  #honduras | el canciller anuncio la llegada de...       None         None   
4  #internacionales | el presidente de colombia, ...       None         None   
5            #karolsevilla #laliarg #kcamexico indio       None         None   
6  #mafiachotana #organizacioncriminal #corrupcio...       None         None   
7        , si tu no quieres, no tiene porque abortar       None         None   
8  -queee? pero si elon musk es judio.\n_y que ac...       None         None   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...       None         None   

  dehumanization extreme_language lack_of_empathy invalidation  
0           None             None            None         None  
1           None             None            None         None  
2           None             None            None         None  
3           None             None            None         None  
4           None             None            None         None  
5           None             None            None         None  
6           None             None            None         None  
7           None             None            None         None  
8           None             None            None         None  
9           None             None            None         None

In [66]:
def generate_multilabel_df(df):
  df["labels"] = np.empty((len(df), len(labels))).tolist()
  for index, row in df.iterrows():
    row_labels = [row[label] for label in labels]
    for i in range(len(labels)):
      df.loc[index, "labels"][i] = row_labels[i]
  return df[["text", "labels"]]
train = generate_multilabel_df(train)
val = generate_multilabel_df(val)
test = generate_multilabel_df(test)
test_final = generate_multilabel_df(test_final)
train.head(10)

text              labels
0  "bueno, tirando"\ny si hay repregunta, entonce...  [0, 0, 0, 0, 0, 0]
1                "caimos en su retorica de indigena"  [0, 0, 0, 0, 0, 0]
2   "cara de indigena sudaca", porque pio asi luego?  [0, 0, 0, 0, 0, 0]
3  "violar a una nina es menos grave que un abort...  [0, 1, 0, 1, 0, 0]
4              "yo decido quien es judio y quien no"  [1, 0, 1, 0, 0, 0]
5  #8m e cada dia en defensa dun xornalismo femin...  [0, 0, 0, 0, 0, 0]
6  #chvnoticias la muerte de ninos no se transa p...  [0, 0, 1, 0, 1, 0]
7  #corrupcion#prensa#desestabilizadora#nido#rata...  [1, 1, 0, 0, 0, 1]
8  #ecuador | la cancilleria implementa plan de a...  [0, 0, 0, 0, 0, 0]
9  #importante | te decimos la ubicacion de los 1...  [0, 0, 0, 0, 0, 0]

In [67]:
test.head(10)

text  \
0  "puta weon, los progres arruinaron el indio pi...   
1  #mexico | el gobierno informo que esta dialoga...   
2               a abortar el mojon que traen atorado   
3             a comerrrrr\n(la salsa es curry indio)   
4                         aborto libre y retroactivo   
5  ah, veo que te has saltado las secuelas y el r...   
6            ase sina y corrupta , ella y su sequito   
7                           chak de india\n#indvseng   
8          coincred, a digital india.\n#coincredweb3   
9  corrupcion, corrupcion corrutos corrutos corru...   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [68]:
test_final.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [70]:
test = test_final
test.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                                 labels  
0  [None, None, None, None, None, None]  
1  [None, None, None, None, None, None]  
2  [None, None, None, None, None, None]  
3  [None, None, None, None, None, None]  
4  [None, None, None, None, None, None]  
5  [None, None, None, None, None, None]  
6  [None, None, None, None, None, None]  
7  [None, None, None, None, None, None]  
8  [None, None, None, None, None, None]  
9  [None, None, None, None, None, None]

In [71]:
from datetime import datetime, timedelta
import os
PATH = "./outputs/{}/".format((datetime.now() + timedelta(hours=2)).strftime("%d-%m-%Y-%H-%M"))
print("Current working dir:", PATH)
os.mkdir(PATH)

Current working dir: ./outputs/31-01-2026-22-58/


In [72]:
models = {
    "mbert-cased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-cased"
    },
    "mbert-uncased": {
        "model_type": "bert",
        "model_name": "models--google-bert--bert-base-multilingual-uncased"
    },
    "roberta": {
        "model_type": "roberta",
        "model_name": "models--FacebookAI--roberta-base"
    },
    "beto-cased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-cased"
    },
    "beto-uncased": {
        "model_type": "bert",
        "model_name": "models--dccuchile--bert-base-spanish-wwm-uncased"
    },
    "distilbert-multi": {
        "model_type": "distilbert",
        "model_name": "models--distilbert--distilbert-base-multilingual-cased"
    }
}

In [73]:
from simpletransformers.classification import MultiLabelClassificationModel, MultiLabelClassificationArgs
for model, fields in models.items():
  model_args = MultiLabelClassificationArgs(
      overwrite_output_dir= True,
      eval_batch_size=8,
      num_train_epochs=5,
      learning_rate = 4e-05,
      optimizer="AdamW",
      manual_seed=SEED,
      use_early_stopping=True,
      save_model_every_epoch=False
  )
  model_args.output_dir = os.path.join(PATH, model)
  models[model] = MultiLabelClassificationModel(fields["model_type"], fields["model_name"],
                                      args=model_args, num_labels=len(labels), use_cuda=use_cuda)

Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of BertForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--google-bert--bert-base-multilingual-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaForMultiLabelSequenceClassification were not initialized from the model checkpoint at models--FacebookAI--roberta-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.dense.bias', 'roberta.pooler.dense.weight', 'classifier.dense.weight', 'roberta.pooler.dense.bias', 'classifier.out_

In [74]:
from sklearn.metrics import mean_squared_error
from math import sqrt
def root_mean_squared_error(y_true, y_pred):    
  return sqrt(mean_squared_error(y_true, y_pred))

In [ ]:
for model_name, model in models.items():
  model.train_model(train, loss_fct=root_mean_squared_error)

7it [00:04,  1.50it/s]                                                                                                                                                                                                                  
Epoch 5 of 5: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 5/5 [02:35<00:00, 31.06s/it]
7it [00:05,  1.24it/s]                                                                                                                                                                                                                  
Epochs 2/5. Running Loss:    0.4039:  64%|███████████████████████████████████████████████████████████████████████████████████████████████████                                                         | 263/414 [00:19<00:10, 14.70it/s]

Epoch 5 of 5: 100%|████████████████████████████████████████████████

In [78]:
import collections
from itertools import combinations
models_names = list(models.keys())
ensembles_list = list()
for i in range(1, len(models_names) + 1):
    ensembles_list += list(combinations(models_names, i))
ensembles_list = [list(ensemble) for ensemble in ensembles_list]
ensembles = {}
for i in range(len(ensembles_list)):
  ensembles["ensemble{:02d}".format(i)] = {}
  ensembles["ensemble{:02d}".format(i)]["models"] = ensembles_list[i]
  ensembles["ensemble{:02d}".format(i)]["metrics"] = {}
ensembles

{'ensemble00': {'models': ['mbert-cased'], 'metrics': {}},
 'ensemble01': {'models': ['mbert-uncased'], 'metrics': {}},
 'ensemble02': {'models': ['roberta'], 'metrics': {}},
 'ensemble03': {'models': ['beto-cased'], 'metrics': {}},
 'ensemble04': {'models': ['beto-uncased'], 'metrics': {}},
 'ensemble05': {'models': ['distilbert-multi'], 'metrics': {}},
 'ensemble06': {'models': ['mbert-cased', 'mbert-uncased'], 'metrics': {}},
 'ensemble07': {'models': ['mbert-cased', 'roberta'], 'metrics': {}},
 'ensemble08': {'models': ['mbert-cased', 'beto-cased'], 'metrics': {}},
 'ensemble09': {'models': ['mbert-cased', 'beto-uncased'], 'metrics': {}},
 'ensemble10': {'models': ['mbert-cased', 'distilbert-multi'], 'metrics': {}},
 'ensemble11': {'models': ['mbert-uncased', 'roberta'], 'metrics': {}},
 'ensemble12': {'models': ['mbert-uncased', 'beto-cased'], 'metrics': {}},
 'ensemble13': {'models': ['mbert-uncased', 'beto-uncased'], 'metrics': {}},
 'ensemble14': {'models': ['mbert-uncased', 'd

In [79]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, f1_score
def compute_metrics(y_true, y_pred):
  macro_precision, macro_recall, macro_f1, _ = precision_recall_fscore_support(y_true, y_pred, average='macro')
  acc = accuracy_score(y_true, y_pred)
  weighted_f1 = f1_score(y_true, y_pred, average='weighted')
  return {
      'accuracy': round(acc, 5),
      'macro_f1': round(macro_f1, 5),
      'macro_precision': round(macro_precision, 5),
      'macro_recall': round(macro_recall, 5),
      'weighted_f1': round(weighted_f1, 5)
  }
model_evaluation = {}
for model_name in models:
  model_evaluation[model_name] = {}
  result, model_outputs, wrong_predictions = models[model_name].eval_model(val, metric=root_mean_squared_error)
  model_evaluation[model_name]["result"] = result                                                                   
  model_evaluation[model_name]["val_model_outputs"] = model_outputs                                                 
  model_evaluation[model_name]["val_predictions"] = list ()
  for output in model_outputs:
    model_evaluation[model_name]["val_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output]) 
  model_evaluation[model_name]["val_wrong_predictions"] = wrong_predictions                                         
  model_evaluation[model_name]["metrics"] = compute_metrics(val.get("labels").tolist(), model_evaluation[model_name].get("val_predictions"))
  print(f"{model_name}\t", model_evaluation[model_name].get("metrics"))

7it [00:05,  1.31it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 79.79it/s]
C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


mbert-cased	 {'accuracy': 0.48593, 'macro_f1': 0.09524, 'macro_precision': 0.21917, 'macro_recall': 0.06901, 'weighted_f1': 0.13432}


7it [00:04,  1.42it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 78.27it/s]


mbert-uncased	 {'accuracy': 0.68502, 'macro_f1': 0.78183, 'macro_precision': 0.80908, 'macro_recall': 0.76351, 'weighted_f1': 0.80199}


7it [00:04,  1.48it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:05<00:00, 78.93it/s]
C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


...

beto-cased	 {'accuracy': 0.83419, 'macro_f1': 0.90314, 'macro_precision': 0.92223, 'macro_recall': 0.8869, 'weighted_f1': 0.91059}


7it [00:04,  1.55it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:04<00:00, 84.43it/s]


beto-uncased	 {'accuracy': 0.89652, 'macro_f1': 0.94597, 'macro_precision': 0.95126, 'macro_recall': 0.94179, 'weighted_f1': 0.94973}


7it [00:04,  1.50it/s]                                                                                                                                                                                                                  
Running Evaluation: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 414/414 [00:03<00:00, 126.47it/s]


distilbert-multi	 {'accuracy': 0.66717, 'macro_f1': 0.7647, 'macro_precision': 0.80855, 'macro_recall': 0.7337, 'weighted_f1': 0.78447}


In [80]:
from sklearn.preprocessing import normalize
def vote(predictions, weighted=False, weights=None):
  votes = list()  
  for i in range(len(labels)):    
    curr_label_preds = [preds[i] for preds in predictions]    
    voting = sum(curr_label_preds * weights) if weighted else sum(curr_label_preds)/len(curr_label_preds)
    votes.append(0 if voting < 0.5 else 1)  
  return votes
ensemble_evaluation = {}
def predict_ensemble(ensemble_name, dataset_name, dataset, weighted=False):
  ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"] = list()  
  for i in range(len(dataset.index)):
    predictions = list()
    ensemble_models = ensembles[ensemble_name].get("models")      
    for model_name in ensemble_models:
      curr_model_outputs = model_evaluation[model_name].get(f"{dataset_name}_model_outputs")
      predictions.append(curr_model_outputs[i])
    weights = list()    
    if weighted:      
      f1_scores_list = [model_evaluation[model_name]["metrics"].get("weighted_f1")                        
                        for model_name in ensembles[ensemble_name].get("models")]
      weights = normalize([f1_scores_list], norm="l1")[0]
    ensemble_pred = vote(predictions, weighted, weights)
    ensemble_evaluation[ensemble_name][f"{dataset_name}_predictions"].append(ensemble_pred)
for ensemble_name in ensembles:
  ensemble_evaluation[ensemble_name] = {}
  ensemble_evaluation[ensemble_name]["val_predictions"] = list()
  predict_ensemble(ensemble_name, "val", val, weighted=WEIGHTED)
  ensembles[ensemble_name]["metrics"] = compute_metrics(val.get("labels").tolist(), ensemble_evaluation[ensemble_name].get("val_predictions"))  
  print(f"{ensemble_name}\t", ensembles[ensemble_name].get("metrics"))

C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


ensemble00	 {'accuracy': 0.48593, 'macro_f1': 0.09524, 'macro_precision': 0.21917, 'macro_recall': 0.06901, 'weighted_f1': 0.13432}
ensemble01	 {'accuracy': 0.68502, 'macro_f1': 0.78183, 'macro_precision': 0.80908, 'macro_recall': 0.76351, 'weighted_f1': 0.80199}


C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


ensemble02	 {'accuracy': 0.49773, 'macro_f1': 0.0, 'macro_precision': 0.0, 'macro_recall': 0.0, 'weighted_f1': 0.0}
ensemble03	 {'accuracy': 0.83419, 'macro_f1': 0.90314, 'macro_precision': 0.92223, 'macro_recall': 0.8869, 'weighted_f1': 0.91059}
ensemble04	 {'accuracy': 0.89652, 'macro_f1': 0.94597, 'macro_precision': 0.95126, 'macro_recall': 0.94179, 'weighted_f1': 0.94973}
ensemble05	 {'accuracy': 0.66717, 'macro_f1': 0.7647, 'macro_precision': 0.80855, 'macro_recall': 0.7337, 'weighted_f1': 0.78447}
ensemble06	 {'accuracy': 0.67776, 'macro_f1': 0.76978, 'macro_precision': 0.82968, 'macro_recall': 0.72927, 'weighted_f1': 0.79385}


C:\Users\8888\Anaconda3\envs\SemEval2025_Task11\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


ensemble07	 {'accuracy': 0.48593, 'macro_f1': 0.09524, 'macro_precision': 0.21917, 'macro_recall': 0.06901, 'weighted_f1': 0.13432}
ensemble08	 {'accuracy': 0.82844, 'macro_f1': 0.89611, 'macro_precision': 0.93396, 'macro_recall': 0.86554, 'weighted_f1': 0.90592}
ensemble09	 {'accuracy': 0.89319, 'macro_f1': 0.94165, 'macro_precision': 0.95632, 'macro_recall': 0.92938, 'weighted_f1': 0.94699}
ensemble10	 {'accuracy': 0.65749, 'macro_f1': 0.74022, 'macro_precision': 0.83343, 'macro_recall': 0.68437, 'weighted_f1': 0.7679}
ensemble11	 {'accuracy': 0.68502, 'macro_f1': 0.78183, 'macro_precision': 0.80908, 'macro_recall': 0.76351, 'weighted_f1': 0.80199}
ensemble12	 {'accuracy': 0.80454, 'macro_f1': 0.88343, 'macro_precision': 0.9154, 'macro_recall': 0.85823, 'weighted_f1': 0.89358}
ensemble13	 {'accuracy': 0.8711, 'macro_f1': 0.92657, 'macro_precision': 0.94034, 'macro_recall': 0.91535, 'weighted_f1': 0.93448}
ensemble14	 {'accuracy': 0.69803, 'macro_f1': 0.79327, 'macro_precision': 0.841

In [81]:
import json
with open(os.path.join(PATH, 'ensembles.json'), 'w', encoding='utf-8') as f:
    json.dump(ensembles, f, ensure_ascii=False, indent=4)

In [82]:
f1_scores = {ensemble_name: ensembles[ensemble_name]["metrics"].get("weighted_f1") for ensemble_name in ensemble_evaluation}
best_ensemble_name = max(f1_scores, key=f1_scores.get)
best_ensemble = {"name": best_ensemble_name,                 
                "models": ensembles[best_ensemble_name].get("models"),                 
                "metrics": ensembles[best_ensemble_name].get("metrics")                 
                }
best_ensemble

{'name': 'ensemble18',
 'models': ['beto-cased', 'beto-uncased'],
 'metrics': {'accuracy': 0.90469,
  'macro_f1': 0.9484,
  'macro_precision': 0.95785,
  'macro_recall': 0.94031,
  'weighted_f1': 0.95304}}

In [83]:
for model_name in models:
  model_predictions, model_raw_outputs = models.get(model_name).predict(test["text"].tolist())
  model_evaluation[model_name]["test_model_outputs"] = model_raw_outputs
  model_evaluation[model_name]["test_predictions"] = list ()  
  for output in model_raw_outputs:
    model_evaluation[model_name]["test_predictions"].append([0 if lab_output < 0.5 else 1 for lab_output in output])
predict_ensemble(best_ensemble.get("name"), "test", test, weighted=WEIGHTED)

3it [00:04,  1.37s/it]                                                                                                                                                                                                                  
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 186/186 [00:03<00:00, 60.44it/s]
3it [00:03,  1.29s/it]                                                                                                                                                                                                                  
100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 186/186 [00:02<00:00, 69.13it/s]
3it [00:03,  1.20s/it]                                              

In [84]:
for model_name, evaluation in model_evaluation.items():
  curr_model = model_evaluation.get(model_name)
  curr_model["val_model_outputs"] = [list(output) for output in curr_model.get("val_model_outputs")]
  curr_model["test_model_outputs"] = [list(output) for output in curr_model.get("test_model_outputs")]
  curr_model["val_predictions"] = list(curr_model.get("val_predictions"))
  curr_model["test_predictions"] = list(curr_model.get("test_predictions"))
  if curr_model.get("val_wrong_predictions"):
    curr_model["val_wrong_predictions_list"] = curr_model.get("val_wrong_predictions")
    curr_model["val_wrong_predictions"] = {}
    for pred in curr_model.get("val_wrong_predictions_list"):
      curr_model["val_wrong_predictions"][pred.guid] = {
          "text_a": pred.text_a,
          "text_b": pred.text_b,
          "label": pred.label
      }
    del curr_model["val_wrong_predictions_list"]

  with open(os.path.join(PATH, f'{model_name}/model-evaluation.json'), 'w', encoding='utf-8') as f:
    json.dump(curr_model, f, ensure_ascii=False, indent=4)

In [85]:
best_ensemble["val_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("val_predictions")
best_ensemble["test_predictions"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
with open(os.path.join(PATH, 'best-ensemble.json'), 'w', encoding='utf-8') as f:
    json.dump(best_ensemble, f, ensure_ascii=False, indent=4)

In [86]:
test["predicted_labels"] = ensemble_evaluation[best_ensemble.get("name")].get("test_predictions")
test.head(10)

text  \
0  "penas severas para el aborto porque yo estuve...   
1              "si eres pobre debes abortar" eso lei   
2  #brasil exige a #eeuu "respeto" para repatriad...   
3  #honduras | el canciller anuncio la llegada de...   
4  #internacionales | el presidente de colombia, ...   
5            #karolsevilla #laliarg #kcamexico indio   
6  #mafiachotana #organizacioncriminal #corrupcio...   
7        , si tu no quieres, no tiene porque abortar   
8  -queee? pero si elon musk es judio.\n_y que ac...   
9  1978: corrupcion\n1986: corrupcion\n2022: corr...   

                                 labels    predicted_labels  
0  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
1  [None, None, None, None, None, None]  [0, 0, 0, 0, 1, 0]  
2  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
3  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
4  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
5  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
6  [None, None, None, None, None, None]  [1, 1, 0, 0, 0, 1]  
7  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
8  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]  
9  [None, None, None, None, None, None]  [0, 0, 0, 0, 0, 0]

In [87]:
test.to_csv(os.path.join(PATH, "test-predictions.csv"), index=False)  